# Unternehmensregister

## Fetch Auszug

In [118]:
import os
from pathlib import Path

from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC

search_query = "GEA Farm Technologies"

options = webdriver.ChromeOptions()

download_path = str(Path(Path.cwd() / "data" / "Unternehmensregister"))
print(download_path)

preferences = {
    "profile.default_content_settings.popups": 0,
    "safebrowsing.enabled": True,
    "download": {
        "directory_upgrade": True,
        "prompt_for_download": False,
        "extensions_to_open": "",
        "default_directory": download_path,
    },
}
options.add_experimental_option("prefs", preferences)

driver = webdriver.Chrome(options=options)

driver.get("https://www.unternehmensregister.de/ureg/")
# Accept Cookies
driver.find_elements(
    By.XPATH, '//button[text()="Nur technisch notwendige Cookies akzeptieren"]'
)[0].click()
# Enter search query
driver.find_elements(By.ID, "globalSearchForm:extendedResearchCompanyName")[
    0
].send_keys(search_query)
# Trigger search
driver.find_elements(By.ID, "globalSearchForm:btnExecuteSearchOld")[0].click()
# Wait for results
wait = WebDriverWait(driver, 5)
wait.until(
    lambda driver: driver.current_url != "https://www.unternehmensregister.de/ureg/"
)
## TODO Iterate over tabs
num_pages = int(
    driver.find_element(By.XPATH, '//*[@class="page_count"]').text.split(" ")[0]
)
for page_index in range(num_pages):
    # Find all "Registerinformationen"
    companies_tab = driver.find_elements(
        By.LINK_TEXT, "Registerinformationen des Registergerichts"
    )
    for company_link in companies_tab:
        # Go to intermediary page
        company_link.click()
        # Trigger next redirect
        driver.find_element(By.LINK_TEXT, "Registerinformationen anzeigen").click()
        # Trigger SI download
        driver.find_element(By.LINK_TEXT, "SI").click()
        # Show shopping cart - TODO evaluate restructuring behaviour by filling cart first and then bulk downloading
        wait.until(
            EC.visibility_of_element_located((By.LINK_TEXT, "Dokumentenkorb ansehen"))
        )
        driver.find_element(By.LINK_TEXT, "Dokumentenkorb ansehen").click()
        # Get document
        xpath = "//input[@type='submit']"
        elems = driver.find_elements(By.TAG_NAME, "input")
        elems[-2].click()

        driver.find_element(By.ID, "paymentFormOverview:btnNext").click()
        driver.find_element(By.LINK_TEXT, "Zum Dokumentenkorb").click()
        driver.find_element(By.CLASS_NAME, "download-wrapper").click()

        for i in range(6):
            driver.back()
    driver.find_element(By.XPATH, '//*[@class="fas fa-angle-right"]').click()
driver.close()

c:\Users\trist\Documents\Code\M.Sc\aki_prj23_transparenzregister\Jupyter\API-tests\Unternehmensregister\data\Unternehmensregister


## Analyze Auszug

In [119]:
files = os.listdir("./data/Unternehmensregister")
files

['registerdocument-2023-06-09-14-05-01.xml',
 'registerdocument-2023-06-09-14-05-03.xml']

In [135]:
import json
import xmltodict

for file in files:
    with open("./data/Unternehmensregister/" + file, "r", encoding="utf-8") as xml_file:
        data = xmltodict.parse(xml_file.read())
        with open("./data/temp.json", "w", encoding="utf-8") as json_file:
            json_file.write(json.dumps(data))

        keys = dict.keys(data["XJustiz_Daten"]["Grunddaten"])
        base_info = {
            "company_name": data["XJustiz_Daten"]["Fachdaten_Register"][
                "Basisdaten_Register"
            ]["Rechtstraeger"]["Bezeichnung"]["Bezeichnung_Aktuell"],
            "location": {
                "city": data["XJustiz_Daten"]["Fachdaten_Register"][
                    "Basisdaten_Register"
                ]["Rechtstraeger"]["Anschrift"]["Ort"],
                "zip_code": data["XJustiz_Daten"]["Fachdaten_Register"][
                    "Basisdaten_Register"
                ]["Rechtstraeger"]["Anschrift"]["Postleitzahl"],
                "street": data["XJustiz_Daten"]["Fachdaten_Register"][
                    "Basisdaten_Register"
                ]["Rechtstraeger"]["Anschrift"]["Strasse"],
                "house_number": data["XJustiz_Daten"]["Fachdaten_Register"][
                    "Basisdaten_Register"
                ]["Rechtstraeger"]["Anschrift"]["Hausnummer"],
            },
        }

        def parse_stakeholder(data: dict) -> list:
            if "Natuerliche_Person" in data["Beteiligter"]:
                return {
                    "name": {
                        "firstname": data["Beteiligter"]["Natuerliche_Person"][
                            "Voller_Name"
                        ]["Vorname"],
                        "lastname": data["Beteiligter"]["Natuerliche_Person"][
                            "Voller_Name"
                        ]["Nachname"],
                    },
                    "date_of_birth": data["Beteiligter"]["Natuerliche_Person"][
                        "Geburt"
                    ]["Geburtsdatum"],
                    "location": {
                        "city": data["Beteiligter"]["Natuerliche_Person"]["Anschrift"][
                            "Ort"
                        ]
                    },
                    "role": data["Rolle"]["Rollenbezeichnung"]["content"],
                }
            return {}

        for i in range(
            len(data["XJustiz_Daten"]["Grunddaten"]["Verfahrensdaten"]["Beteiligung"])
        ):
            people = parse_stakeholder(
                data["XJustiz_Daten"]["Grunddaten"]["Verfahrensdaten"]["Beteiligung"][i]
            )
            print(people)
    break

{}
{}
{'name': {'firstname': 'Reinhard', 'lastname': 'Gebing'}, 'date_of_birth': '1964-04-26', 'location': {'city': 'Oelde'}, 'role': 'Prokurist(in)'}
{'name': {'firstname': 'Markus', 'lastname': 'Kreft'}, 'date_of_birth': '1966-04-03', 'location': {'city': 'Wetter'}, 'role': 'Prokurist(in)'}
{'name': {'firstname': 'Kai', 'lastname': 'Luntz'}, 'date_of_birth': '1970-12-04', 'location': {'city': 'Holzminden'}, 'role': 'Prokurist(in)'}
{'name': {'firstname': 'Thomas', 'lastname': 'Mader'}, 'date_of_birth': '1972-05-24', 'location': {'city': 'Rheda-Wiedenbrück'}, 'role': 'Prokurist(in)'}
{'name': {'firstname': 'Peter', 'lastname': 'Lauwers'}, 'date_of_birth': '1970-03-26', 'location': {'city': 'Düsseldorf'}, 'role': 'Geschäftsführer(in)'}
{'name': {'firstname': 'Erkul', 'lastname': 'Basaran'}, 'date_of_birth': '1977-05-06', 'location': {'city': 'Erkrath'}, 'role': 'Geschäftsführer(in)'}
{'name': {'firstname': 'Katja', 'lastname': 'Voß'}, 'date_of_birth': '1978-02-24', 'location': {'city':

In [27]:
from pdf2image import convert_from_path

pdfs = r"./data/test.pdf"
pages = convert_from_path(pdfs, 350)


for i, page in enumerate(pages):
    image_name = f"./data/Page_{i+1}.jpg"
    page.save(image_name, "JPEG")

In [28]:
import cv2
import pytesseract

image_path = "./data/Page_1.jpg"
image = cv2.imread(image_path)

text = str(pytesseract.image_to_string(image, config="--psm 6", lang="deu"))
print(text)
with open("./data/Page_1.txt", "w", encoding="utf-8") as output_file:
    output_file.write(text)

Handelsregister B des Abteilung B Nummer der Firma:
Amtsgerichts Hamm Wiedergabe des aktuellen HRB 5363
Registerinhalts
Abruf vom 07.06.2023 19:37
1. Anzahl der bisherigen Eintragungen:
51
2. a) Firma:
GEA Farm Technologies GmbH
b) Sitz, Niederlassung, inländische Geschäftsanschrift, empfangsberechtigte Person, Zweigniederlassungen:
Bönen
Geschäftsanschrift: Siemensstraße 25-27, 59199 Bönen
c) Gegenstand des Unternehmens:
Entwicklung, Herstellung und der Vertrieb von Landtechnik, insbesondere von Komponenten und Anlagen
(a) zur Gewinnung, Kühlung, Behandlung und Lagerung von Milch;
(b) für das Milchvieh-Herdenmanagement;
(c) zur Tierhygiene und Sicherung der Milchqualität und
(d) zur Aufstallung von Tieren;
sowie die Herstellung und der Vertrieb von Anlagen und Fahrzeugen zur Aufbereitung und zum Transport von Gülle.
3. Grund- oder Stammkapital:
5.115.000,00 EUR
4. a) Allgemeine Vertretungsregelung:
Ist nur ein Geschäftsführer bestellt, so vertritt er die Gesellschaft allein. Sind mehr

In [29]:
import re


def get_managing_directors(text: str) -> list:
    managing_directors_regex = r"Geschäftsführer: [a-zA-ZäöüÄÖÜ]*, [a-zA-ZäöüÄÖÜ]*"
    hits = re.findall(managing_directors_regex, text)
    print(hits)
    return [
        " ".join(hit.replace("Geschäftsführer: ", "").replace(",", "").split(" ")[::-1])
        for hit in hits
    ]


get_managing_directors(text)

['Geschäftsführer: Basaran, Erkul', 'Geschäftsführer: Cheng, Liang', 'Geschäftsführer: Lauwers, Peter']


['Erkul Basaran', 'Liang Cheng', 'Peter Lauwers']